In [1]:
import nltk
import re
from nltk.corpus import stopwords
import pandas as pd
import gensim

directory = '../WebScraper/mycarforum/'

# Get all filenames
corpus = nltk.corpus.PlaintextCorpusReader(directory, '.+\.txt')
fids = corpus.fileids()

isVectorBuild = False

fids

['mycarforumpost1.txt',
 'mycarforumpost10.txt',
 'mycarforumpost100.txt',
 'mycarforumpost101.txt',
 'mycarforumpost102.txt',
 'mycarforumpost103.txt',
 'mycarforumpost104.txt',
 'mycarforumpost105.txt',
 'mycarforumpost106.txt',
 'mycarforumpost107.txt',
 'mycarforumpost108.txt',
 'mycarforumpost109.txt',
 'mycarforumpost11.txt',
 'mycarforumpost110.txt',
 'mycarforumpost111.txt',
 'mycarforumpost112.txt',
 'mycarforumpost113.txt',
 'mycarforumpost114.txt',
 'mycarforumpost115.txt',
 'mycarforumpost116.txt',
 'mycarforumpost117.txt',
 'mycarforumpost118.txt',
 'mycarforumpost119.txt',
 'mycarforumpost12.txt',
 'mycarforumpost120.txt',
 'mycarforumpost121.txt',
 'mycarforumpost122.txt',
 'mycarforumpost123.txt',
 'mycarforumpost124.txt',
 'mycarforumpost125.txt',
 'mycarforumpost126.txt',
 'mycarforumpost127.txt',
 'mycarforumpost128.txt',
 'mycarforumpost129.txt',
 'mycarforumpost13.txt',
 'mycarforumpost130.txt',
 'mycarforumpost131.txt',
 'mycarforumpost132.txt',
 'mycarforumpost13

In [10]:
corpus = []
data_df = pd.DataFrame(columns=["User","Reputation","Posts_Count","Comment","Date"])


for fid in fids:
    thread = []
    with open(directory + fid, encoding="utf8") as file:
        lines = file.readlines()
        if lines:
            forum_content = []
            # Remove default html & encoding values
            for row in lines:
                row = row.replace("\n","")
                row = row.replace("\t","")
                row = row.replace("\xa0","")
                forum_content.append(row)
            forum_content = list(filter(None, forum_content))
            content_dict = {}
            post_list = []
            for i,content in enumerate(forum_content):
                if "total reputation" in content:
                    post_list.append(content_dict)
                    content_dict = {}
                    content_dict[str(i)] = content
                elif content == " ":
                    continue
                else:
                    content_dict[str(i)] = content
            post_list.pop(0)
            for posts_dict in post_list:
                counter = 0
                row_list = []
                comments = ""
                for dict_value in posts_dict.values():
                    if counter <= 2:
                        counter += 1
                        row_list.append(dict_value)
                    else:
                        comments += dict_value
                date = comments[comments.find("Edited"):comments.find("by")]
                date_stuff = comments[comments.find("Edited"):]
                comments = comments.replace(date_stuff,"")
                comments = comments.replace("Edited","")
                row_list.append(comments)
                row_list.append(date)
                data_df.loc[len(data_df)] = row_list
                

In [25]:
thread = data_df["Comment"].tolist()

In [26]:
corpus.append(thread)

In [27]:
stop_list = nltk.corpus.stopwords.words('english')
my_stopwords = ['Comments', 'answerAnswerBump']

tokenized = []

# Tokenization
for thread in corpus:
    tokens = [nltk.word_tokenize(post) for post in thread]
    tokenized.append(tokens)
    
    
# Pre-processing
cleaned_corpus = []
    
for thread in tokenized:
    cleaned_thread = [[w.lower() for w in post] for post in thread]
    cleaned_thread = [[w for w in post if re.search('^[a-z]+$', w)] for post in cleaned_thread]
    cleaned_thread = [[w for w in post if w not in stop_list and w not in my_stopwords] for post in cleaned_thread]
    cleaned_corpus.append(cleaned_thread)
    
cleaned_corpus

[[[],
  ['g'],
  ['r'],
  ['e'],
  ['e'],
  ['p'],
  ['r'],
  [],
  ['c'],
  ['e'],
  [],
  [],
  ['h'],
  ['e'],
  ['n'],
  ['g'],
  ['e'],
  [],
  ['v'],
  [],
  ['l'],
  ['u'],
  [],
  [],
  [],
  [],
  ['n'],
  ['f'],
  [],
  ['r'],
  ['h'],
  [],
  ['b'],
  ['r'],
  ['e'],
  [],
  [],
  ['l'],
  ['e'],
  [],
  ['e'],
  [],
  ['l'],
  [],
  ['p'],
  ['u'],
  ['b'],
  ['l'],
  [],
  [],
  ['h'],
  ['e'],
  [],
  [],
  ['n'],
  [],
  [],
  ['r'],
  [],
  [],
  [],
  [],
  [],
  [],
  [],
  ['b'],
  [],
  ['j'],
  [],
  ['n'],
  [],
  ['c'],
  ['e'],
  ['h'],
  ['e'],
  ['n'],
  ['g'],
  ['c'],
  [],
  [],
  ['h'],
  [],
  [],
  ['v'],
  ['e'],
  ['r'],
  [],
  ['v'],
  [],
  ['l'],
  ['u'],
  [],
  [],
  [],
  [],
  ['n'],
  [],
  ['c'],
  [],
  ['v'],
  [],
  ['f'],
  [],
  ['g'],
  ['u'],
  ['r'],
  ['e'],
  [],
  ['w'],
  [],
  ['l'],
  ['l'],
  ['n'],
  [],
  ['l'],
  [],
  ['n'],
  ['g'],
  ['e'],
  ['r'],
  ['b'],
  ['e'],
  ['p'],
  [],
  ['r'],
  [],
  [],
  ['f'],
  [],
  ['

In [28]:
# Create dictionary
dictionary = gensim.corpora.Dictionary()
for thread in cleaned_corpus:
    dictionary.add_documents(thread)
#     print(dictionary.token2id)

# Collapse thread into bow
corpus_bow = []
for thread in cleaned_corpus:
    thread_bow = []
    for post in thread:
        for word in post:
            thread_bow.append(word)
    corpus_bow.append(thread_bow)

# Term document frequency
tdf = [dictionary.doc2bow(thread) for thread in corpus_bow]
tdf

[[(0, 24),
  (1, 56),
  (2, 86),
  (3, 21),
  (4, 17),
  (5, 35),
  (6, 62),
  (7, 17),
  (8, 51),
  (9, 32),
  (10, 14),
  (11, 21),
  (12, 1),
  (13, 14),
  (14, 4),
  (15, 1),
  (16, 2)],
 [(0, 3),
  (1, 2),
  (2, 5),
  (3, 1),
  (4, 2),
  (5, 4),
  (6, 4),
  (7, 1),
  (8, 3),
  (9, 1),
  (10, 1),
  (13, 2)],
 [(1, 3), (2, 3), (3, 4), (5, 1), (8, 5), (9, 2)],
 [(0, 4),
  (1, 6),
  (2, 12),
  (3, 2),
  (4, 5),
  (5, 7),
  (6, 9),
  (7, 4),
  (8, 4),
  (9, 3),
  (10, 3),
  (13, 3)],
 [(0, 6),
  (1, 19),
  (2, 38),
  (3, 9),
  (4, 8),
  (5, 18),
  (6, 25),
  (7, 10),
  (8, 19),
  (9, 12),
  (10, 7),
  (11, 11),
  (12, 1),
  (13, 10),
  (14, 6)],
 [(0, 3),
  (1, 3),
  (2, 8),
  (3, 1),
  (4, 4),
  (6, 5),
  (7, 1),
  (8, 4),
  (9, 1),
  (10, 1),
  (11, 1),
  (13, 3),
  (14, 2)],
 [(0, 1),
  (1, 6),
  (2, 17),
  (3, 2),
  (4, 8),
  (5, 7),
  (7, 5),
  (8, 3),
  (9, 6),
  (10, 3),
  (13, 4),
  (14, 1)],
 [(0, 7),
  (1, 30),
  (2, 72),
  (3, 11),
  (4, 20),
  (5, 34),
  (6, 45),
  (7, 17),

In [29]:
# Build LDA model
lda_model = gensim.models.ldamodel.LdaModel(corpus=tdf,
                                           id2word=dictionary,
                                           num_topics=3, 
                                           random_state=100,
                                           update_every=1,
                                           chunksize=3,
                                           passes=10,
                                           alpha='auto',
                                           per_word_topics=True)

KeyboardInterrupt: 

In [ ]:
# Print the Keyword in the 10 topics
print(lda_model.print_topics())